In [12]:
# Function to create tick values and labels
import pandas as pd
import numpy as np
import plotly.graph_objects as go
from plotly.subplots import make_subplots

def extract_rtt(row):
    if row['success']:
        try:
            return float(row['rtt'].replace('ms', ''))
        except (ValueError, AttributeError):
            return np.nan
    return 0.1  # Return 0.1 for failed pings instead of 0

# Function to calculate automatic rolling window based on percentage of data
def calculate_rolling_window(df, percentage=1.5):
    return int(len(df) * percentage / 100)

def create_ticks(max_power):
    tick_values = [0.1] + [10**i for i in range(0, max_power + 1)]
    tick_labels = ['0'] + [f'10^{i}' for i in range(0, max_power + 1)]
    return tick_values, tick_labels

# Load logs into a DataFrame
df = pd.read_csv('logs-example.csv', header=None, 
                names=['timestamp', 'success', 'host', 'ip', 'packetsize', 'rtt', 'ttl'])

# Convert 'timestamp' to datetime with specified format
df['timestamp'] = pd.to_datetime(df['timestamp'], format='ISO8601', utc=True, errors='coerce')

# Convert 'success' to boolean
df['success'] = df['success'].astype(str).str.lower() == 'true'

# Modify timestamp to match the correct timezone
df['timestamp'] = df['timestamp'].dt.tz_convert('Europe/Helsinki')

# Apply the function to create a new 'rtt_value' column
df['rtt_value'] = df.apply(extract_rtt, axis=1)

# Sort DataFrame by timestamp
df = df.sort_values('timestamp')

# Set rolling window
MANUAL_ROLLING_WINDOW = None  # Set this to a value if you want to manually specify the window
ROLLING_WINDOW = MANUAL_ROLLING_WINDOW if MANUAL_ROLLING_WINDOW is not None else calculate_rolling_window(df)

# Calculate rolling averages separately for success and failure
df['rolling_avg_success'] = df[df['success']]['rtt_value'].rolling(window=ROLLING_WINDOW, center=True).mean()
df['rolling_avg_failure'] = df[~df['success']]['rtt_value'].rolling(window=ROLLING_WINDOW, center=True).mean()

# Calculate overall average RTT
average_rtt = df[df['success']]['rtt_value'].mean()

# Calculate the highest point of the successful rolling line
highest_rtt = df['rolling_avg_success'].max()

# Adjust this value to change the number of tick values
MAX_POWER = 4  # This will create ticks: 0.1, 1, 10, 100, 1000, 10000

tick_values, tick_labels = create_ticks(MAX_POWER)

# Create the plot
fig = make_subplots(specs=[[{"secondary_y": True}]])

# Create separate DataFrames for successful and failed pings
df_success = df[df['success']]
df_failure = df[~df['success']]

df_success_avg = df_success.groupby('timestamp')['rtt_value'].mean().reset_index()

# Add scatter plot for successful pings (averaged)
fig.add_trace(go.Scatter(
    x=df_success_avg['timestamp'],
    y=df_success_avg['rtt_value'],
    mode='markers',
    name='Success',
    marker=dict(color='blue', size=5),
    hovertemplate='RTT: %{y:.2f} ms<br>Timestamp: %{x}<extra></extra>',
    visible=True
))

# Add scatter plot for failed pings
fig.add_trace(go.Scatter(
    x=df_failure['timestamp'],
    y=[0.1] * len(df_failure),  # Use 0.1 to make failures visible on log scale
    mode='markers',
    name='Failure',
    marker=dict(color='red', size=5),
    hovertemplate='Failure<br>Timestamp: %{x}<extra></extra>',
    visible=True
))

# Add rolling average line for successful pings
fig.add_trace(go.Scatter(
    x=df['timestamp'],
    y=df['rolling_avg_success'].combine_first(df['timestamp'].map(lambda x: average_rtt)),
    mode='lines',
    name=f'Rolling Avg (Success, window={ROLLING_WINDOW})',
    line=dict(color='green', width=2),
    hovertemplate='Rolling Avg RTT: %{y:.2f} ms<br>Timestamp: %{x}<extra></extra>',
    hoverlabel=dict(namelength=0)
))

# Add rolling average line for failed pings
fig.add_trace(go.Scatter(
    x=df['timestamp'],
    y=df['rolling_avg_failure'],
    mode='lines',
    name=f'Rolling Avg (Failure, window={ROLLING_WINDOW})',
    line=dict(color='purple', width=3),
    hovertemplate='Rolling Avg RTT: Failed Ping! (0ms)<br>Timestamp: %{x}<extra></extra>'
))

# Add average RTT line
fig.add_trace(go.Scatter(
    x=[df['timestamp'].min(), df['timestamp'].max()],
    y=[average_rtt] * 2,
    mode='lines',
    name=f'Average RTT: {average_rtt:.2f} ms',
    line=dict(color="orange", width=2, dash="dash"),
    hovertemplate='Average RTT: %{y:.2f} ms<br>Timestamp: %{x}<extra></extra>'
))

# Add horizontal line for highest RTT
fig.add_trace(go.Scatter(
    x=[df['timestamp'].min(), df['timestamp'].max()],
    y=[highest_rtt] * 2,
    mode='lines',
    name=f'Highest RTT: {highest_rtt:.2f} ms',
    line=dict(color="gray", width=1, dash="dash"),
    hovertemplate='Highest RTT: %{y:.2f} ms<br>Timestamp: %{x}<extra></extra>'
))

# Get current timestamp
current_time = pd.Timestamp.now().strftime("%Y-%m-%d %H:%M:%S")

# Update layout with logarithmic Y-axis and timestamp
fig.update_layout(
    title=f'Ping Results (Generated: {current_time})',
    xaxis_title='Timestamp',
    yaxis_title='RTT (ms)',
    yaxis=dict(
        type='log',
        tickmode='array',
        tickvals=tick_values,
        ticktext=tick_labels,
        range=[np.log10(0.1), np.log10(10**MAX_POWER)]
    ),
    showlegend=True,
    updatemenus=[
        dict(
            type="buttons",
            direction="right",
            active=0,
            x=0.7,  # Moved buttons more to the right
            y=1.2,
            buttons=list([
                dict(label="Show Dots",
                    method="update",
                    args=[{"visible": [True, True, True, True, True, True]},
                        {"title": f"Ping Results (Dots Visible) (Generated: {current_time})"}]),
                dict(label="Hide Dots",
                    method="update",
                    args=[{"visible": [False, False, True, True, True, True]},
                        {"title": f"Ping Results (Dots Hidden) (Generated: {current_time})"}]),
            ]),
        )
    ]
)

# Show the plot
fig.show()

In [5]:
# Perform data analysis
def analyze_data(df):
    analysis = "Data Analysis Report\n"
    analysis += "=" * 20 + "\n\n"

    # Add timestamp and author
    current_time = pd.Timestamp.now().strftime("%Y-%m-%d %H:%M:%S")
    analysis += f"Generated on: {current_time}\n"
    analysis += "Author: Maksim Shabunov\n\n"

    # Basic statistics
    analysis += "1. Basic Statistics:\n"
    analysis += f"   Total data points: {len(df)}\n"
    analysis += f"   Successful pings: {df['success'].sum()}\n"
    analysis += f"   Failed pings: {len(df) - df['success'].sum()}\n"
    analysis += f"   Success rate: {df['success'].mean()*100:.2f}%\n\n"

    # RTT statistics
    rtt_stats = df[df['success']]['rtt_value'].describe()
    analysis += "2. RTT Statistics (for successful pings):\n"
    analysis += f"   Mean RTT: {rtt_stats['mean']:.2f} ms\n"
    analysis += f"   Median RTT: {rtt_stats['50%']:.2f} ms\n"
    analysis += f"   Min RTT: {rtt_stats['min']:.2f} ms\n"
    analysis += f"   Max RTT: {rtt_stats['max']:.2f} ms\n"
    analysis += f"   Standard deviation: {rtt_stats['std']:.2f} ms\n\n"

    # Time-based analysis
    df['hour'] = df['timestamp'].dt.hour
    hourly_success_rate = df.groupby('hour')['success'].mean()
    best_hour = hourly_success_rate.idxmax()
    worst_hour = hourly_success_rate.idxmin()
    analysis += "3. Time-based Analysis:\n"
    analysis += f"   Best hour for connectivity: {best_hour}:00 (Success rate: {hourly_success_rate[best_hour]*100:.2f}%)\n"
    analysis += f"   Worst hour for connectivity: {worst_hour}:00 (Success rate: {hourly_success_rate[worst_hour]*100:.2f}%)\n\n"

    # Failure analysis
    failure_runs = df['success'].astype(int).diff().ne(0).cumsum()
    longest_failure = failure_runs[~df['success']].value_counts().max()
    total_failures = len(df) - df['success'].sum()
    failure_rate = total_failures / len(df) * 100
    avg_failure_duration = failure_runs[~df['success']].value_counts().mean()
    analysis += "4. Failure Analysis:\n"
    analysis += f"   Total failures: {total_failures}\n"
    analysis += f"   Failure rate: {failure_rate:.2f}%\n"
    analysis += f"   Longest continuous failure streak: {longest_failure} pings\n"
    analysis += f"   Average failure duration: {avg_failure_duration:.2f} pings\n"
    analysis += f"   Percentage of time in failure state: {(total_failures / len(df)) * 100:.2f}%\n\n"

    # Success analysis
    success_runs = df['success'].astype(int).diff().ne(0).cumsum()
    longest_success = success_runs[df['success']].value_counts().max()
    total_successes = df['success'].sum()
    success_rate = total_successes / len(df) * 100
    avg_success_duration = success_runs[df['success']].value_counts().mean()
    analysis += "5. Success Analysis:\n"
    analysis += f"   Total successful pings: {total_successes}\n"
    analysis += f"   Success rate: {success_rate:.2f}%\n"
    analysis += f"   Longest continuous success streak: {longest_success} pings\n"
    analysis += f"   Average success duration: {avg_success_duration:.2f} pings\n"
    analysis += f"   Percentage of time in success state: {(total_successes / len(df)) * 100:.2f}%\n\n"

    # Trend analysis
    first_half = df[:len(df)//2]
    second_half = df[len(df)//2:]
    trend = "improving" if second_half['success'].mean() > first_half['success'].mean() else "deteriorating"
    analysis += "6. Trend Analysis:\n"
    analysis += f"   Overall trend: Connection stability is {trend}\n"
    
    return analysis

# Generate the analysis report
analysis_report = analyze_data(df)

# Print the analysis report directly
print(analysis_report)

Data Analysis Report

Generated on: 2024-07-06 12:43:53
Author: Maksim Shabunov

1. Basic Statistics:
   Total data points: 40602
   Successful pings: 18117
   Failed pings: 22485
   Success rate: 44.62%

2. RTT Statistics (for successful pings):
   Mean RTT: 53.03 ms
   Median RTT: 46.00 ms
   Min RTT: 2.00 ms
   Max RTT: 1643.00 ms
   Standard deviation: 75.33 ms

3. Time-based Analysis:
   Best hour for connectivity: 15:00 (Success rate: 78.32%)
   Worst hour for connectivity: 5:00 (Success rate: 2.69%)

4. Failure Analysis:
   Total failures: 22485
   Failure rate: 55.38%
   Longest continuous failure streak: 381 pings
   Average failure duration: 120.89 pings
   Percentage of time in failure state: 55.38%

5. Success Analysis:
   Total successful pings: 18117
   Success rate: 44.62%
   Longest continuous success streak: 734 pings
   Average success duration: 97.93 pings
   Percentage of time in success state: 44.62%

6. Trend Analysis:
   Overall trend: Connection stability is det

In [3]:
import plotly.graph_objects as go
import plotly.subplots as sp
import numpy as np
import pandas as pd

# Calculate success and failure rates
total_pings = len(df)
success_rate = df['success'].sum() / total_pings * 100
failure_rate = 100 - success_rate

# Create a figure with subplots
fig = sp.make_subplots(
    rows=3,
    cols=1,
    specs=[[{"type": "domain"}], [{"type": "xy"}], [{"type": "xy"}]],
    subplot_titles=(
        'Success vs Failure Rate',
        'Hourly Success Rate',
        'Cumulative Success Rate Over Time'
    )
)

# 1. Success vs Failure Rate
labels = ['Success', 'Failure']
values = [success_rate, failure_rate]
colors = ['#66b3ff', '#ff9999']

fig.add_trace(
    go.Pie(
        labels=labels,
        values=values,
        marker=dict(colors=colors),
        hovertemplate='%{label}: %{value:.1f}%<extra></extra>'  # Remove trace 0 text on hover
    ),
    row=1, col=1
)

# 2. Hourly Success Rate
df['hour'] = df['timestamp'].dt.hour
hourly_success_rate = df.groupby('hour')['success'].mean() * 100

fig.add_trace(
    go.Bar(
        x=hourly_success_rate.index,
        y=hourly_success_rate.values,
        marker_color='#4169E1',
        name='Success Rate by Hour'
    ),
    row=2, col=1
)

fig.update_yaxes(title_text="Success Rate (%)", range=[0, 100], row=2, col=1)

# 3. Trend Analysis
df['cumulative_success_rate'] = df['success'].cumsum() / (df.index + 1)

fig.add_trace(
    go.Scatter(
        x=df.index,
        y=df['cumulative_success_rate'] * 100,
        mode='lines',
        line=dict(color='#66b3ff'),
        name='Cumulative Success Rate'
    ),
    row=3, col=1
)

fig.update_yaxes(title_text="Cumulative Success Rate (%)", range=[0, 100], row=3, col=1)
fig.update_xaxes(title_text="Ping Number", row=3, col=1)

# Update layout
fig.update_layout(height=900, width=800, title_text="Data Analysis Visualization")

# Show the plot
fig.show()